
# NeuralkAI Classifier Workflow Example

This example demonstrates how to use the NeuralkAI SDK to:

1. Create a new project.
2. Upload a synthetic classification dataset (two moons).
3. Launch and monitor a classifier training analysis.
4. Download training results.
5. Launch and monitor a classifier prediction analysis.
6. Download prediction results.

We use scikit-learn's ``make_moons`` dataset to simulate a binary classification task.


## Step 1 - Import required libraries



In [ ]:
import os
import polars as pl
import tempfile
from pathlib import Path
import matplotlib.pyplot as plt
from sklearn.metrics import accuracy_score
import numpy as np

from neuralk import Neuralk
from neuralk.datasets import two_moons

## Step 2 - Load credentials and connect to the NeuralkAI platform
Instead of hardcoding your credentials, you should store them securely in environment variables.

The most common approaches are:

1. **Environment variables in the operating system**

- On Linux/macOS with Bash::

    export NEURALK_USER=your_username
    export NEURALK_PASSWORD=your_password

- On Windows (Command Prompt)::

    set NEURALK_USER=your_username
    set NEURALK_PASSWORD=your_password

2. **Using a '.env' file** (useful during development)

- Create a file named ``.env`` in the root of your project with::

    NEURALK_USER=your_username
    NEURALK_PASSWORD=your_password

- Then use ``python-dotenv`` to load these variables into your environment.
- Don’t forget to add ``.env`` to your ``.gitignore`` to avoid committing it.

We try to load the ``.env`` file automatically, but if it’s not available, the code still works
as long as the variables are set in the system environment.



In [ ]:
try:
    # Try to load .env file if python-dotenv is available
    from dotenv import load_dotenv

    load_dotenv()
except ImportError:
    print("python-dotenv not installed, skipping .env loading")

user = os.environ.get("NEURALK_USER")
password = os.environ.get("NEURALK_PASSWORD")

assert (
    user is not None and password is not None
), "Missing NEURALK_USER or NEURALK_PASSWORD. Set them in your environment or a .env file."

client = Neuralk(user, password)

## Step 4 - Create a new project and upload precomputed moons dataset



In [ ]:
for project in client.projects.get_list():
    if project.name == "MoonsExample":
        client.projects.delete(project)

project = client.projects.create("MoonsExample")
print("Project created:", project)

moons_data = two_moons()
print(moons_data["path"])

dataset = client.datasets.create(
    project,
    "MoonsExample",
    moons_data["path"],
    )
print("Dataset uploaded:", dataset)

## Step 5 - Create a classifier training analysis
We specify the column to predict ("label") and the features to use.



In [ ]:
analysis_fit = client.analysis.create_classifier_fit(
    dataset,
    "Two Moons Classifier",
    target_column="label",
    feature_column_name_list=["feature1", "feature2"],
)
print("Classifier training analysis created:", analysis_fit)

## Step 6 - Wait for training to complete
We monitor the training progress until it's complete.



In [ ]:
analysis_fit = client.analysis.wait_until_complete(analysis_fit, verbose=True)

## Step 7 - Launch a prediction analysis
We reuse the same dataset and model to perform predictions.



In [ ]:
analysis_predict = client.analysis.create_classifier_predict(
    dataset, "Two Moons Prediction", analysis_fit
)
print("Prediction analysis launched:", analysis_predict)
analysis_predict = client.analysis.wait_until_complete(analysis_predict,
                                                       verbose=True)

## Step 8 - Download prediction results



In [ ]:
with tempfile.TemporaryDirectory() as results_dir:
    client.analysis.download_results(analysis_predict, folder_path=results_dir)
    print("Prediction results downloaded to temporary directory")
    results_file = next(Path(results_dir).iterdir())
    y_pred = pl.read_parquet(results_file)["label"].to_numpy()[:, 0]

X = pl.read_csv(moons_data["path"])
y = X["label"].to_numpy()
X = X.drop("label").to_numpy()

acc = accuracy_score(y, y_pred)
print(f"Accuracy of classification: {acc}")

## Step 9 - Plot the results



In [ ]:
plt.rcParams.update(
    {
        "axes.edgecolor": "#4d4d4d",
        "axes.linewidth": 1.2,
        "axes.facecolor": "#f5f5f5",
        "figure.facecolor": "white",
    }
)

fig, axes = plt.subplots(1, 2, figsize=(11, 5), dpi=120)
titles = ["Ground Truth", f"Model Prediction\nAccuracy: {acc:.2f}"]
colors = ["#1a73e8", "#ffa600"]  # Professional blue & orange

for idx, ax in enumerate(axes):
    labels = y if idx == 0 else y_pred
    for lab in np.unique(labels):
        ax.scatter(
            X[labels == lab, 0],
            X[labels == lab, 1],
            s=70,
            marker="o",
            c=colors[lab],
            edgecolors="white",
            linewidths=0.8,
            alpha=0.9,
            label=f"Class {lab}" if idx == 0 else None,  # Legend only on first panel
            zorder=3,
        )

    # Aesthetics
    ax.set_xticks([])
    ax.set_yticks([])
    ax.set_aspect("equal")
    ax.set_title(titles[idx], fontsize=14, weight="bold", pad=12)
    ax.grid(False)

    # Subtle outer border (inside the axes limits)
    x_margin = 0.4
    y_margin = 0.4
    ax.set_xlim(X[:, 0].min() - x_margin, X[:, 0].max() + x_margin)
    ax.set_ylim(X[:, 1].min() - y_margin, X[:, 1].max() + y_margin)

    # Panel annotation (A, B)
    ax.text(
        0.05,
        0.98,
        chr(ord("A") + idx),
        transform=ax.transAxes,
        fontsize=16,
        fontweight="bold",
        va="top",
        ha="right",
    )

# Shared legend beneath the plots
handles, labels_ = axes[0].get_legend_handles_labels()
fig.legend(
    handles,
    labels_,
    loc="lower center",
    ncol=2,
    frameon=False,
    fontsize=12,
    bbox_to_anchor=(0.5, 0.02),
)

fig.tight_layout()
plt.subplots_adjust(bottom=0.05)
plt.show()

## Step 10 - Clean the environement



In [ ]:
client.logout()